In [36]:
import os, sys
# project_path = '../'
PWD = os.getenv('PWD')
# os.chdir(project_path)
sys.path.insert(0, PWD)
# sys.path.insert(0, project_path)
print(sys.path)
# os.environ.setdefault("DJANGO_SETTINGS_MODULE", "settings.py")
import django
django.setup()

['/Users/russmo/Code/mpatlas-dj2/mpatlas', '/Users/russmo/Code/mpatlas-dj2/mpatlas', '/Users/russmo/Code/mpatlas-dj2/mpatlas/notebooks', '/usr/local/Cellar/python/3.7.5/Frameworks/Python.framework/Versions/3.7/lib/python37.zip', '/usr/local/Cellar/python/3.7.5/Frameworks/Python.framework/Versions/3.7/lib/python3.7', '/usr/local/Cellar/python/3.7.5/Frameworks/Python.framework/Versions/3.7/lib/python3.7/lib-dynload', '', '/Users/russmo/.venvs/mpa/lib/python3.7/site-packages', '/Users/russmo/.venvs/mpa/lib/python3.7/site-packages/IPython/extensions', '/Users/russmo/.ipython']


In [ ]:
%%javascript

window.scroll_flag = true
window.scroll_exit = false
window.scroll_delay = 100

$(".output_scroll").each(function() {
    $(this)[0].scrollTop = $(this)[0].scrollHeight;
});

function callScrollToBottom() {
    setTimeout(scrollToBottom, window.scroll_delay);
}

function scrollToBottom() {
    if (window.scroll_exit) {
        return;
    }
    if (!window.scroll_flag) {
        callScrollToBottom();
        return;
    };
    
    $(".output_scroll").each(function() {
        if (!$(this).attr('scroll_checkbox')){
            window.scroll_flag = true;
            $(this).attr('scroll_checkbox',true);
            var div = document.createElement('div');
            var checkbox = document.createElement('input');
            checkbox.type = "checkbox";
            checkbox.onclick = function(){window.scroll_flag = checkbox.checked}
            checkbox.checked = "checked"
            div.append("Auto-Scroll-To-Bottom: ");
            div.append(checkbox);
            $(this).parent().before(div);
        }
        
        $(this)[0].scrollTop = $(this)[0].scrollHeight;
    });
    callScrollToBottom();
}
scrollToBottom();

In [37]:
from mpa.models import Mpa, mpa_post_save
from django.db.models.signals import post_save, post_delete
from mpa.views import mpas_all_nogeom
import reversion
from reversion.models import Revision
from reversion.models import Version
import datetime
from django.db.models import Q, F, Func
from wdpa.models import WdpaPoly_prev, WdpaPoint_prev
from wdpa.models import WdpaPoly_new, WdpaPoint_new

In [39]:
# logprefix = 'home/mpatlas/workspace/log/'
logprefix = '/Users/russmo/Code/wdpa/log/'

In [40]:
mpaset = mpas_all_nogeom.exclude(
        Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
        Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
        Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
        Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
        Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
        Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
        Q(country__icontains='MNP') | Q(sovereign__icontains='MNP') |
        Q(country__icontains='CHL') | Q(sovereign__icontains='CHL')
    ).filter(Q())
mpaset.values('country').distinct()

<QuerySet [{'country': 'ABNJ'}, {'country': 'MDG'}, {'country': 'TZA'}, {'country': 'PLW'}, {'country': 'GGY'}, {'country': 'NLD'}, {'country': 'VEN'}, {'country': 'BMU'}, {'country': 'FIN/SWE'}, {'country': 'COG'}, {'country': 'CUB'}, {'country': 'MAF'}, {'country': 'IRL'}, {'country': 'GIB'}, {'country': 'IOT'}, {'country': 'ISR'}, {'country': 'GBR'}, {'country': 'BGD/IND'}, {'country': 'MMR'}, {'country': 'GMB'}, '...(remaining elements truncated)...']>

In [4]:
# mpaset = mpas_all_nogeom.exclude(
#         Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
#         Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
#         Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
#         Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
#         Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
#         Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
#         Q(country__icontains='MNP') | Q(sovereign__icontains='MNP')
#     ).exclude(
#         Q(country__icontains='MEX') | Q(country__icontains='CHL') | Q(country__icontains='IDN') | 
#         Q(country__icontains='CHN') | Q(country__icontains='JPN') | 
#         Q(sovereign__icontains='MEX') | Q(sovereign__icontains='CHL') | Q(sovereign__icontains='IDN') |
#         Q(sovereign__icontains='CHN') | Q(sovereign__icontains='JPN')
#     ).exclude(
#         Q(country__icontains='FRA') | Q(sovereign__icontains='FRA') |
#         Q(country__icontains='ATF') | Q(country__icontains='BLM') | Q(country__icontains='GLP') |
#         Q(country__icontains='GUF') | Q(country__icontains='MAF') | Q(country__icontains='MTQ') |
#         Q(country__icontains='MYT') | Q(country__icontains='NCL') | Q(country__icontains='PYF') |
#         Q(country__icontains='REU') | Q(country__icontains='SHN') | Q(country__icontains='SYC')
#     ).exclude(
#         Q(country__icontains='AUS') | Q(sovereign__icontains='AUS') |
#         Q(country__icontains='ZAF') | Q(sovereign__icontains='ZAF') |
#         Q(country__icontains='CAN') | Q(sovereign__icontains='CAN')
#     ).exclude(
#         Q(country__icontains='GBR') | Q(sovereign__icontains='GBR') |
#         Q(country__icontains='AIA') | Q(country__icontains='BMU') | Q(country__icontains='CYM') |
#         Q(country__icontains='FLK') | Q(country__icontains='GIB') | Q(country__icontains='IMN') |
#         Q(country__icontains='IOT') | Q(country__icontains='JEY') | Q(country__icontains='MSR') |
#         Q(country__icontains='PCN') | Q(country__icontains='SGS') | Q(country__icontains='SHN') |
#         Q(country__icontains='TCA') | Q(country__icontains='VGB')
#     )
# mpaset.values('country').distinct()

In [41]:
mpas_all_nogeom.filter(wdpa_id=0).update(wdpa_id=None)
mpas_all_nogeom.filter(wdpa_id=0).count()

0

In [42]:
count = 0
# cutoff_date = datetime.datetime(2018, 10, 15)
cutoff_date = datetime.datetime(2019, 12, 30)
for m in mpaset:
    versions = Version.objects.get_for_object(m)
    created = 'Never'
    if not m.wdpa_id: continue
    try:
        created = versions.first().revision.date_created
        if created > cutoff_date:
            count = count + 1
            print(count, created, 'count:', len(versions), 'mpa_id:', m.mpa_id, 'wdpa_id:', m.wdpa_id)
    except:
        pass

1 2019-12-31 13:29:21.632148 count: 1 mpa_id: 68813844 wdpa_id: 136810
2 2019-12-30 14:47:37.438174 count: 1 mpa_id: 68813512 wdpa_id: 156768
3 2019-12-31 15:55:11.250726 count: 1 mpa_id: 6223 wdpa_id: 13261
4 2019-12-31 15:55:22.209450 count: 1 mpa_id: 6321 wdpa_id: 14258
5 2019-12-30 14:47:42.060883 count: 1 mpa_id: 68813598 wdpa_id: 31469
6 2019-12-31 15:58:17.870137 count: 1 mpa_id: 9658 wdpa_id: 555547752
7 2020-01-01 17:20:09.414325 count: 1 mpa_id: 15124 wdpa_id: 555559749
8 2019-12-31 14:18:14.100502 count: 1 mpa_id: 68815684 wdpa_id: 555538466
9 2019-12-31 13:30:32.157738 count: 1 mpa_id: 68813880 wdpa_id: 138532
10 2019-12-30 14:47:42.416295 count: 1 mpa_id: 68813604 wdpa_id: 3552
11 2019-12-30 14:47:42.521097 count: 1 mpa_id: 68813606 wdpa_id: 3583
12 2019-12-31 15:54:41.902640 count: 1 mpa_id: 5851 wdpa_id: 1125
13 2020-10-13 11:52:58.099537 count: 1 mpa_id: 68808360 wdpa_id: 345888
14 2020-01-01 14:23:18.255535 count: 1 mpa_id: 4395 wdpa_id: 309888
15 2019-12-30 14:47:42.4

126 2019-12-31 15:56:09.185935 count: 1 mpa_id: 7001 wdpa_id: 305497
127 2020-01-01 14:12:42.445629 count: 1 mpa_id: 3920 wdpa_id: 305590
128 2019-12-31 15:57:38.252738 count: 1 mpa_id: 9537 wdpa_id: 555547631
129 2019-12-31 15:58:22.786206 count: 1 mpa_id: 9674 wdpa_id: 555549147
130 2019-12-30 14:47:37.487316 count: 1 mpa_id: 68813513 wdpa_id: 157236
131 2020-01-01 14:20:58.725691 count: 1 mpa_id: 4335 wdpa_id: 308677
132 2019-12-31 15:56:25.544568 count: 1 mpa_id: 7707123 wdpa_id: 315526
133 2020-01-01 14:14:31.866799 count: 1 mpa_id: 7704019 wdpa_id: 305993
134 2019-12-31 15:59:19.236787 count: 1 mpa_id: 6009 wdpa_id: 9257
135 2019-12-31 15:57:00.161669 count: 1 mpa_id: 7705928 wdpa_id: 4244
136 2020-01-01 13:07:13.586361 count: 1 mpa_id: 1172 wdpa_id: 14013
137 2020-01-01 14:12:17.557024 count: 1 mpa_id: 7703902 wdpa_id: 305439
138 2020-01-01 21:52:14.373343 count: 1 mpa_id: 15513 wdpa_id: 555576574
139 2020-01-01 13:08:10.341357 count: 1 mpa_id: 68809816 wdpa_id: 14078
140 2020-0

259 2019-12-31 13:43:40.787255 count: 1 mpa_id: 68814380 wdpa_id: 176610
260 2020-01-01 14:11:56.914154 count: 1 mpa_id: 3889 wdpa_id: 305374
261 2020-01-01 14:12:10.518299 count: 1 mpa_id: 7703898 wdpa_id: 305418
262 2020-01-01 16:54:36.734099 count: 1 mpa_id: 14583 wdpa_id: 555548087
263 2020-01-01 14:12:11.530208 count: 1 mpa_id: 3898 wdpa_id: 305418
264 2019-12-31 15:57:27.449033 count: 1 mpa_id: 7526 wdpa_id: 555542776
265 2020-01-01 22:48:02.506032 count: 1 mpa_id: 68813165 wdpa_id: 555629251
266 2020-01-01 22:48:03.679670 count: 1 mpa_id: 68813166 wdpa_id: 555629252
267 2019-12-31 13:30:58.691050 count: 1 mpa_id: 68813893 wdpa_id: 139836
268 2020-01-01 14:12:15.571147 count: 1 mpa_id: 3901 wdpa_id: 305438
269 2019-12-31 15:57:49.382546 count: 1 mpa_id: 9572 wdpa_id: 555547666
270 2020-01-01 14:12:16.510598 count: 1 mpa_id: 7703901 wdpa_id: 305438
271 2019-12-31 15:57:49.736415 count: 1 mpa_id: 9573 wdpa_id: 555547667
272 2020-01-01 12:51:24.042931 count: 1 mpa_id: 1106 wdpa_id: 

397 2020-01-01 22:42:23.980898 count: 1 mpa_id: 68810629 wdpa_id: 555624410
398 2020-01-01 16:54:28.685393 count: 1 mpa_id: 14580 wdpa_id: 555548076
399 2020-01-01 12:50:36.523814 count: 1 mpa_id: 7701057 wdpa_id: 12989
400 2020-01-01 16:55:43.246852 count: 1 mpa_id: 14608 wdpa_id: 555548178
401 2020-01-01 12:50:37.453668 count: 1 mpa_id: 1057 wdpa_id: 12989
402 2020-01-01 14:11:49.331628 count: 1 mpa_id: 7703885 wdpa_id: 305351
403 2020-01-01 15:00:53.583268 count: 1 mpa_id: 6 wdpa_id: 42
404 2020-01-01 16:55:36.442148 count: 1 mpa_id: 14607 wdpa_id: 555548176
405 2020-01-01 22:46:18.684002 count: 1 mpa_id: 68813087 wdpa_id: 555624691
406 2020-01-01 16:55:47.837881 count: 1 mpa_id: 68808825 wdpa_id: 555548181
407 2020-01-01 16:55:54.174848 count: 1 mpa_id: 68808828 wdpa_id: 555548182
408 2020-01-01 13:30:28.094207 count: 1 mpa_id: 3310 wdpa_id: 166935
409 2020-01-01 12:36:16.955720 count: 1 mpa_id: 789 wdpa_id: 10092
410 2020-01-01 13:30:28.980618 count: 1 mpa_id: 3311 wdpa_id: 166936

522 2020-01-01 22:55:30.941667 count: 1 mpa_id: 2036 wdpa_id: 63908
523 2020-01-01 12:50:25.006176 count: 1 mpa_id: 1051 wdpa_id: 12982
524 2020-01-01 12:50:23.902125 count: 1 mpa_id: 7701051 wdpa_id: 12982
525 2020-01-01 23:10:24.292320 count: 1 mpa_id: 6768 wdpa_id: 81034
526 2020-01-01 23:09:49.232406 count: 1 mpa_id: 109 wdpa_id: 763
527 2020-01-01 12:46:24.510138 count: 1 mpa_id: 2813 wdpa_id: 127679
528 2019-12-31 15:56:21.379376 count: 1 mpa_id: 7088 wdpa_id: 313512
529 2020-01-01 14:35:46.085807 count: 1 mpa_id: 7701859 wdpa_id: 34314
530 2020-01-01 14:40:04.502747 count: 1 mpa_id: 4926 wdpa_id: 351821
531 2020-01-01 14:13:13.018702 count: 1 mpa_id: 3950 wdpa_id: 305789
532 2020-01-01 23:10:16.822244 count: 1 mpa_id: 6759 wdpa_id: 81025
533 2020-01-01 13:57:43.898389 count: 1 mpa_id: 6920 wdpa_id: 220011
534 2020-01-01 23:10:15.949259 count: 1 mpa_id: 6758 wdpa_id: 81024
535 2019-12-31 15:56:22.722846 count: 1 mpa_id: 7092 wdpa_id: 313530
536 2020-01-01 13:57:45.597782 count: 1

...

18898 2020-01-01 16:53:55.209523 count: 1 mpa_id: 14571 wdpa_id: 555548046
18899 2020-01-01 13:17:13.994904 count: 1 mpa_id: 3096 wdpa_id: 152392
18900 2020-01-01 13:33:47.149919 count: 1 mpa_id: 68809853 wdpa_id: 170023
18901 2020-01-01 16:57:22.367165 count: 1 mpa_id: 14628 wdpa_id: 555548840
18902 2020-01-01 14:24:43.429069 count: 1 mpa_id: 4730 wdpa_id: 313361
18903 2020-01-01 15:23:49.875584 count: 1 mpa_id: 12575 wdpa_id: 555522470
18904 2020-01-01 16:54:37.795940 count: 1 mpa_id: 68808801 wdpa_id: 555548087
18905 2020-01-01 15:43:23.242579 count: 1 mpa_id: 12973 wdpa_id: 555527958
18906 2020-01-01 16:55:06.988516 count: 1 mpa_id: 68808810 wdpa_id: 555548146
18907 2020-01-01 16:55:18.427721 count: 1 mpa_id: 68808815 wdpa_id: 555548152
18908 2020-01-01 16:57:24.078401 count: 1 mpa_id: 14630 wdpa_id: 555548842
18909 2020-01-01 13:34:54.400403 count: 1 mpa_id: 10678 wdpa_id: 170431
18910 2020-01-01 13:34:55.419986 count: 1 mpa_id: 10679 wdpa_id: 170434
18911 2020-01-01 16:55:41.2653

19028 2020-01-01 22:00:46.773274 count: 1 mpa_id: 15752 wdpa_id: 555578655
19029 2020-01-01 17:14:24.180728 count: 1 mpa_id: 68812209 wdpa_id: 555558360
19030 2020-01-01 16:14:06.758500 count: 1 mpa_id: 13629 wdpa_id: 555538234
19031 2020-01-01 14:33:44.278802 count: 1 mpa_id: 11444 wdpa_id: 339241
19032 2020-01-01 13:37:30.945856 count: 1 mpa_id: 3382 wdpa_id: 173501
19033 2020-01-01 14:32:26.630792 count: 1 mpa_id: 11384 wdpa_id: 330445
19034 2020-01-01 13:26:50.192553 count: 1 mpa_id: 10619 wdpa_id: 156617
19035 2020-01-01 13:40:36.308399 count: 1 mpa_id: 1334 wdpa_id: 17757
19036 2020-01-01 14:37:36.818756 count: 1 mpa_id: 68811152 wdpa_id: 348878
19037 2020-01-01 12:46:42.412306 count: 1 mpa_id: 986 wdpa_id: 12782
19038 2020-01-01 17:18:15.059087 count: 1 mpa_id: 15076 wdpa_id: 555559213
19039 2020-01-01 13:37:46.055805 count: 1 mpa_id: 10735 wdpa_id: 173665
19040 2020-01-01 13:41:45.636787 count: 1 mpa_id: 10876 wdpa_id: 181130
19041 2020-01-01 21:54:22.967922 count: 1 mpa_id: 15

19147 2020-01-01 13:51:02.128068 count: 1 mpa_id: 11163 wdpa_id: 195452
19148 2020-01-01 16:28:37.133621 count: 1 mpa_id: 13904 wdpa_id: 555540810
19149 2020-01-01 12:43:54.789773 count: 1 mpa_id: 2745 wdpa_id: 125925
19150 2020-01-01 16:44:02.584634 count: 1 mpa_id: 14055 wdpa_id: 555543111
19151 2020-01-01 23:03:33.266421 count: 1 mpa_id: 2335 wdpa_id: 68171
19152 2020-01-01 15:52:15.204337 count: 1 mpa_id: 68811606 wdpa_id: 555531142
19153 2019-12-31 13:22:10.012489 count: 1 mpa_id: 8800894 wdpa_id: 11663
19154 2020-01-01 15:26:14.732639 count: 1 mpa_id: 12641 wdpa_id: 555523039
19155 2020-01-01 14:27:45.079099 count: 1 mpa_id: 7704816 wdpa_id: 315046
19156 2020-01-01 16:30:15.720552 count: 1 mpa_id: 68811956 wdpa_id: 555541109
19157 2020-01-01 15:54:45.048700 count: 1 mpa_id: 13341 wdpa_id: 555532739
19158 2020-01-01 14:36:36.705591 count: 1 mpa_id: 11555 wdpa_id: 345898
19159 2020-01-01 16:29:14.127651 count: 1 mpa_id: 68811932 wdpa_id: 555540883
19160 2020-01-01 23:03:39.359589 c

19262 2020-01-01 21:59:54.327693 count: 1 mpa_id: 15723 wdpa_id: 555578626
19263 2020-01-01 21:47:26.357227 count: 1 mpa_id: 15149 wdpa_id: 555566864
19264 2020-01-01 16:13:18.991144 count: 1 mpa_id: 13611 wdpa_id: 555538132
19265 2020-01-01 13:35:28.547213 count: 1 mpa_id: 68810863 wdpa_id: 170691
19266 2020-01-01 17:23:50.069474 count: 1 mpa_id: 68812256 wdpa_id: 555563181
19267 2019-12-31 14:21:32.843393 count: 1 mpa_id: 68815804 wdpa_id: 555540238
19268 2019-12-31 14:31:31.369207 count: 1 mpa_id: 68816187 wdpa_id: 555565340
19269 2020-01-01 14:32:27.728964 count: 1 mpa_id: 11385 wdpa_id: 330447
19270 2020-01-01 14:49:17.460055 count: 1 mpa_id: 11867 wdpa_id: 388912
19271 2019-12-30 14:47:41.631194 count: 1 mpa_id: 68813590 wdpa_id: 204550
19272 2019-12-31 13:40:27.754408 count: 1 mpa_id: 68814243 wdpa_id: 169636
19273 2020-01-01 22:23:02.009762 count: 1 mpa_id: 68812524 wdpa_id: 555587194
19274 2019-12-31 15:59:01.427276 count: 1 mpa_id: 7328 wdpa_id: 900847
19275 2019-12-31 15:56:

19379 2019-12-30 14:47:40.773479 count: 1 mpa_id: 68813574 wdpa_id: 201081
19380 2020-01-01 14:18:21.820915 count: 1 mpa_id: 4247 wdpa_id: 307885
19381 2020-01-01 23:10:20.979654 count: 1 mpa_id: 6764 wdpa_id: 81030
19382 2019-12-30 14:47:43.639776 count: 1 mpa_id: 5973 wdpa_id: 5055
19383 2019-12-31 14:31:02.471684 count: 1 mpa_id: 68816165 wdpa_id: 555564998
19384 2019-12-31 14:53:34.008098 count: 1 mpa_id: 68817090 wdpa_id: 555646024
19385 2019-12-31 13:29:52.356828 count: 1 mpa_id: 68813861 wdpa_id: 137756
19386 2020-01-01 22:41:26.722838 count: 1 mpa_id: 68813053 wdpa_id: 555624267
19387 2019-12-31 13:47:21.909275 count: 1 mpa_id: 68814491 wdpa_id: 193946
19388 2019-12-31 15:57:24.160789 count: 1 mpa_id: 7510 wdpa_id: 555542713
19389 2019-12-31 13:30:17.740707 count: 1 mpa_id: 68813872 wdpa_id: 138309
19390 2019-12-31 13:50:43.122846 count: 1 mpa_id: 68814568 wdpa_id: 23532
19391 2020-01-01 13:57:48.095777 count: 1 mpa_id: 3577 wdpa_id: 220017
19392 2019-12-31 13:30:16.666290 coun

In [43]:
from importlib import reload
from wdpa import merge
reload(merge)

<module 'wdpa.merge' from '/Users/russmo/Code/mpatlas-dj2/mpatlas/wdpa/merge.py'>

In [44]:
tas = WdpaPoly_new.objects.filter(wdpa_pid__icontains='345888')
print(tas.count())
for t in tas:
    print(t.wdpaid, t.wdpa_pid, t.name, ',', t.desig, t.marine)

sgs = WdpaPoly_new.objects.filter(name__icontains='South Georgia')
print(sgs.count())
for s in sgs:
    print(s.wdpaid, s.wdpa_pid, s.name, ',', s.desig, s.marine)


1
345888.0 345888 Terres Australes Françaises , Réserve Naturelle Nationale 2
2
555610117.0 555610117 South Georgia , Country Club 0
555547601.0 555547601 South Georgia and South Sandwich Islands Marine Protected Area , Marine Protected Area 2


In [45]:
remove_log = logprefix + 'removewdpa_noUSA_noCHL_2020_log.json'
wdpa2remove = merge.getRemoveWdpaList(logfile=remove_log)

In [46]:
len(wdpa2remove)

606

In [47]:
rm_mpas = Mpa.objects.filter(wdpa_id__in=wdpa2remove).order_by('country')
len(rm_mpas)

606

In [48]:
for m in rm_mpas:
    print(m.mpa_id, m.wdpa_id, m.wdpa_pid, m.country, m.sovereign, m.is_mpa, m.no_take, m.no_take_area, m.name, m.designation_eng)

67706581 32642 32642 AIA GBR True Not Reported 0.0 Mimi Bay Pond Marine Park
7078 313116 313116 AIA GBR True Not Reported 0.0 El Buen Consejo Spanish Galleon Ship Wreck Site Tourism Management Area
6282 14074 14074 AIA GBR True Not Reported 0.0 Sandy Island Marine Park
7477 555512104 555512104 AIA GBR False Not Reported 0.0 Junks Hole Pond Marine Park
6581 32642 32642 AIA GBR False Not Reported 0.0 Mimi Bay Pond Marine Park
67706282 14074 14074 AIA GBR True Not Reported 0.0 Sandy Island Marine Park
6579 32640 32640 AIA GBR False Not Applicable 0.0 Scrub Bay Pond Tourism Management Area
6614 36066 36066 AIA GBR True Not Applicable 0.0 Blowing Point Fish Nursery Reserve
68813320 555558346 None ARG ARG True All None Namuncurá - Banco Burdwood [Buffer Zone] Marine Protected Area
9689 555558346 555558346 ARG ARG True All None Namuncurá - Banco Burdwood [Core Zone] Marine Protected Area
68813321 555558346 None ARG ARG True None None Namuncurá - Banco Burdwood [Transition Zone] Marine Protect

2624 101586 101586_A CAN CAN True Not Applicable 0.0 Wapusk National Park Of Canada National Park
68809356 555516369 555516369_B CAN CAN True Not Reported 0.0 Kilbella Estuary Conservancy Conservancy
68816875 555637787 555637787 CAN CAN True Not Reported 0.0 Île à la Brume Migratory Bird Sanctuary Migratory Bird Sanctuary
68816866 555637727 555637727 CAN CAN True Not Reported 0.0 Baie Des Loups Migratory Bird Sanctuary Migratory Bird Sanctuary
68816574 555621551 555621551_A CAN CAN True Not Reported 0.0 Esquimalt Lagoon Migratory Bird Sanctuary Migratory Bird Sanctuary
68809197 13102 13102_B CAN CAN True Not Applicable 0.0 Garden Bay Marine Park A - Park
1392 18503 18503_A CAN CAN True Not Applicable 0.0 Mansons Landing Park A - Park
2079 65425 65425_A CAN CAN True Not Applicable 0.0 Strathcona Park A - Park
68809478 65425 65425_B CAN CAN True Not Reported 0.0 Strathcona Park A - Park
2078 65411 65411_A CAN CAN True Not Applicable 0.0 Smelt Bay Park A - Park
1571 23124 23124_A CAN CAN 

68815678 555538186 555538186 ESP ESP True Not Reported 0.0 Islas Chafarinas Special Protection Area (Birds Directive)
10711 170997 170997 EST EST True Not Reported 0.0 Pakri Mka, Pakri Pv. Limited Management Zone Of Protected Landscape
8800884 11118 11118 GBR GBR False Not Reported None Murlough National Nature Reserve
68813834 136329 136329 GBR GBR True Not Reported 0.0 Seal Sands Site Of Special Scientific Interest (Gb)
68810295 555560487 555560487 GBR GBR True Not Reported 0.0 Rosemary Bank Seamount Nature Conservation Marine Protected Area
890 11611 11611 GNB GNB True Not Reported 0.0 Bijagos Archipelago Biosphere Reserve Biosphere Reserve
9780 33049 33049 GNB GNB True Not Reported 0.0 Cantanhez Forest Hunting Reserve
6292 14190 14190 GRD GRD True Not Reported 0.0 Calivigny Island Local Area Planning
67706292 14190 14190 GRD GRD True Not Reported 0.0 Calivigny Island Local Area Planning
68812479 555582987 555582987 HND HND True Not Reported 0.0 Cuyamel - Omoa National Park
97 715 7

7700367 3148 3148 PNG PNG True Not Reported 0.0 Nanuk Island District Park Provincial Park
7700366 3145 3145 PNG PNG False Not Applicable 0.0 Cape Wom Memorial Park Protected Seascape
9569 555547663 555547663 PNG PNG True Not Applicable 0.0 Pananaru Locally Managed Marine Area
9572 555547666 555547666 PNG PNG True Not Applicable 0.0 Lavongai Locally Managed Marine Area
9571 555547665 555547665 PNG PNG True Not Applicable 0.0 Ngoto Locally Managed Marine Area
9573 555547667 555547667 PNG PNG True Not Applicable 0.0 Tioputuk Locally Managed Marine Area
11675 377711 377711 PNG PNG True Not Reported 0.0 Wewak Peace Memorial Park Protected Seascape
9755 19716 19716 PNG PNG True Not Reported 0.0 Paga Hill National Park Scenic Reserve National Park
366 3145 3145 PNG PNG False Not Applicable 0.0 Cape Wom Memorial Park Protected Seascape
9574 555547668 555547668 PNG PNG True All 0.0 Ungakum Locally Managed Marine Area
9567 555547661 555547661 PNG PNG True Not Applicable 0.0 Machomuna Locally Ma

68810977 198960 198960 RUS RUS True Not Reported 0.0 Von'gomskiy Zakaznik
68810986 200817 200817 RUS RUS True Not Applicable 0.0 Chernye skaly Zakaznik
68810997 201363 201363 RUS RUS True Not Reported 0.0 Dvinskoi Zakaznik
68810978 198961 198961 RUS RUS True Not Reported 0.0 Shuiostrovskiy Zakaznik
68813585 203396 203396 RUS RUS True Not Reported 0.0 Ostrov Starichkov Nature Monument
7701978 62693 None RUS RUS True Not Reported None Ostrov Vrangelya / Wrangel Island Zapovednik
3545 200093 200093 RUS RUS True Not Reported 0.0 Lena-Del'ta Resource Reserve
1856 33395 33395 RUS RUS True Not Reported 0.0 Solovetsky Historical-natural Museum / Zapovednik
3540 200005 200005 RUS RUS True Not Reported 0.0 Peschany Island Resource Reserve (project)
68811032 206793 206793 RUS RUS True Not Reported 0.0 Bukhta Kraternaya Zakaznik
3542 200010 200010 RUS RUS True Not Reported 0.0 Kolyma-Koren Resource Reserve
68810983 200489 200489 RUS RUS True Not Reported 0.0 Tamano-Zaporozhskiy Zakaznik
68810984 2

In [60]:
# Don't remove until we verify that we can lose these records. Canada changed wdpa_ids and/or wdpa_pids
# for lots of sites.  And Argentina's Namuncura/Burdwood Bank I/II changed ids, which breaks things for mpatlas.
# merge.removeMpasByWdpaId(wdpa2remove)

In [49]:
reload(merge)

<module 'wdpa.merge' from '/Users/russmo/Code/mpatlas-dj2/mpatlas/wdpa/merge.py'>

In [50]:
wdpa2add = merge.getAddWdpaList()

In [51]:
len(wdpa2add)

2101

In [52]:
wdpapid2add = merge.getAddWdpaPidList(verbose=True)

70 wdpa_pid's processed
555624907_B : 1 processed
555556896_C : 2 processed
555556903_A : 3 processed
555645309
 : 4 processed
555637831_A : 5 processed
555548008_C : 6 processed
555548008_D : 7 processed
555705062_B : 8 processed
555556876_C : 9 processed
555556906_C : 10 processed
555624907_G : 11 processed
306026_E : 12 processed
555637719_C : 13 processed
313747_A : 14 processed
64056_E : 15 processed
555624907_D : 16 processed
555556903_B : 17 processed
9035_B : 18 processed
555599265_B : 19 processed
64056_D : 20 processed
555621668_A : 21 processed
127159_A : 22 processed
555548008_A : 23 processed
313747_B : 24 processed
555637700_C : 25 processed
18138_A : 26 processed
555637698_D : 27 processed
555577385
 : 28 processed
555556896_A : 29 processed
555621671_D : 30 processed
302326_B : 31 processed
555556885_B : 32 processed
555556894_B : 33 processed
67785_A : 34 processed
24133_C : 35 processed
555556885_A : 36 processed
555548008_E : 37 processed
555624907_C : 38 processed
5

In [53]:
len(wdpapid2add)

70

In [18]:
# Assign records with zones to be the first zone.  Do not rerun.
# In separate notebook

In [54]:
allpid2add = wdpapid2add + [str(int(i)) for i in wdpa2add]
len(allpid2add)
WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2add).count() + \
WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2add).count()

2160

In [55]:
unmatched_pids_poly = WdpaPoly_new.objects.filter(
    Q(wdpa_pid__in=allpid2add) | Q(wdpaid__in=wdpa2add)
).exclude(
    wdpa_pid=Func(F('wdpaid'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')
)
unmatched_pids_point = WdpaPoint_new.objects.filter(
    Q(wdpa_pid__in=allpid2add) | Q(wdpaid__in=wdpa2add)
).exclude(
    wdpa_pid=Func(F('wdpaid'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')
)
unmatched_pids_poly.order_by('wdpa_pid').values_list('wdpaid', 'wdpa_pid')


<QuerySet [(127159.0, '127159_A'), (127159.0, '127159_C'), (18133.0, '18133_A'), (18138.0, '18138_A'), (19963.0, '19963_A'), (24133.0, '24133_A'), (24133.0, '24133_C'), (302326.0, '302326_A'), (302326.0, '302326_B'), (306026.0, '306026_D'), (306026.0, '306026_E'), (309479.0, '309479_C'), (313747.0, '313747_A'), (313747.0, '313747_B'), (555515574.0, '555515574_B'), (555548008.0, '555548008_A'), (555548008.0, '555548008_B'), (555548008.0, '555548008_C'), (555548008.0, '555548008_D'), (555548008.0, '555548008_E'), '...(remaining elements truncated)...']>

In [56]:
# Set wdpa_pid for new zones
# If existing MPAtlas sites with this wdpa_id,
# set first non-rejected site to the first PID_A.
# Clear pid for all other MPAtlas sites and flag
# as orphaned zones.

wzones = []
mpasw = [float(wi) for wi in mpaset.filter(wdpa_id__isnull=False).order_by('wdpa_id').values_list('wdpa_id', flat=True)]
polyset = WdpaPoly_new.objects.filter(wdpaid__in=mpasw).only('wdpaid', 'wdpa_pid', 'name', 'desig_eng', 'iso3', 'parent_iso3')
for w in polyset:
    if w.wdpa_pid != str(int(w.wdpaid)):
        wzones.append(w.wdpaid)
wzones = list(set(wzones))
len(wzones)

164

In [57]:
# Assign mpa records that were previously unzoned to have the pid of the first zone in the updated WDPA data set for this site.
count = 0
for wid in wzones:
    zones = WdpaPoly_new.objects.filter(wdpaid=wid).only('wdpaid', 'wdpa_pid', 'name', 'desig_eng', 'iso3', 'parent_iso3')
    firstpid = zones.order_by('wdpa_pid').first().wdpa_pid
    mpaz = mpaset.filter(wdpa_id=int(wid)).order_by('mpa_id')
    m = None
    if mpaz.filter(wdpa_pid=firstpid).count() == 0:
        # no mpas match first zone pid
        if mpaz.count() == 1:
            if mpaz[0].wdpa_pid == str(mpaz[0].wdpa_id) or mpaz[0].wdpa_pid == '' or mpaz[0].wdpa_pid is None:
                # only record without specific zone, so go ahead and set it first zone
                m = mpaz[0]
        else:
            if mpaz.count() == mpaz.filter(Q(wdpa_pid=Func(F('wdpa_id'), function='INTEGER', template='(%(expressions)s::%(function)s)::text')) | Q(wdpa_pid__isnull=True) | Q(wdpa_pid='')).count():
                # more than one mpatlas mpa record with this wdpa_id
                # but none have a proper wdpa_pid different from the wdpa_id
                # so set first one to have the first zone pid
                nonrejects = mpaz.exclude(verification_state='Rejected as MPA').order_by('mpa_id')
                if nonrejects and nonrejects.count() == 1:
                    m = nonrejects[0]
                else:
                    m = mpaz[0]
    if m:
        print(m.mpa_id, m.wdpa_id, m.wdpa_pid)
        m.wdpa_pid = firstpid
        count += 1
        print(count, m.mpa_id, m.wdpa_id, m.wdpa_pid)
        m.save()


60009465 555624907 None
1 60009465 555624907 555624907_A
Carto Error for mpa_id 60009465: Access denied


In [58]:
reload(merge)
addpoint_geolog = logprefix + 'addpoint_noUSA_noCHL_2020_log.json'
addpoly_log = logprefix + 'addpoly_noUSA_noCHL_2020_log.json'
addpoly_geolog = logprefix + 'addpoly_noUSA_noCHL_2020_geo_log.json'
# addpoint_geolog = '/Users/russmo/Code/wdpa/log/addpoint_TUV_2020_log.json'
# addpoly_log = '/Users/russmo/Code/wdpa/log/addpoly_TUV_2020_v2_zerogeofix_log.json'
# addpoly_geolog = '/Users/russmo/Code/wdpa/log/addpoly_TUV_2020_v2_zerogeofix_geo_log.json'

In [59]:
points = WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2add).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=points, poly=False, logfile=None, geologfile=addpoint_geolog, dryrun=False)

1/1190 adding/updating wdpa_pid 166888 with mpa_id 6875
    PID: 166888 has 4 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6875:  'NoneType' object has no attribute 'hexewkb'
2/1190 adding/updating wdpa_pid 555682395 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817292:  'NoneType' object has no attribute 'hexewkb'
3/1190 adding/updating wdpa_pid 555682425 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817293:  'NoneType' object has no attribute 'hexewkb'
4/1190 adding/updating wdpa_pid 555682458 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817294:  'NoneType' object has no attribute 'hexewkb'
5/1190 adding/updating wdpa_pid 555682872 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817295:  'NoneType' object has no attribute 'hexewkb'
6/1190 adding/updating wdpa_pid 555682874 with mpa_id None
    Retained old MPAtlas values for: 
ERROR

50/1190 adding/updating wdpa_pid 555706010 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817340:  'NoneType' object has no attribute 'hexewkb'
51/1190 adding/updating wdpa_pid 555706012 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817341:  'NoneType' object has no attribute 'hexewkb'
52/1190 adding/updating wdpa_pid 555706013 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817342:  'NoneType' object has no attribute 'hexewkb'
53/1190 adding/updating wdpa_pid 555706014 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817343:  'NoneType' object has no attribute 'hexewkb'
54/1190 adding/updating wdpa_pid 555706015 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817344:  'NoneType' object has no attribute 'hexewkb'
55/1190 adding/updating wdpa_pid 555706016 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 688173

98/1190 adding/updating wdpa_pid 555706060 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817388:  'NoneType' object has no attribute 'hexewkb'
99/1190 adding/updating wdpa_pid 555706061 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817389:  'NoneType' object has no attribute 'hexewkb'
100/1190 adding/updating wdpa_pid 555706062 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817390:  'NoneType' object has no attribute 'hexewkb'
101/1190 adding/updating wdpa_pid 555706063 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817391:  'NoneType' object has no attribute 'hexewkb'
102/1190 adding/updating wdpa_pid 555706064 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817392:  'NoneType' object has no attribute 'hexewkb'
103/1190 adding/updating wdpa_pid 555706065 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68

147/1190 adding/updating wdpa_pid 555706110 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817437:  'NoneType' object has no attribute 'hexewkb'
148/1190 adding/updating wdpa_pid 555706111 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817438:  'NoneType' object has no attribute 'hexewkb'
149/1190 adding/updating wdpa_pid 555706112 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817439:  'NoneType' object has no attribute 'hexewkb'
150/1190 adding/updating wdpa_pid 555706113 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817440:  'NoneType' object has no attribute 'hexewkb'
151/1190 adding/updating wdpa_pid 555706114 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817441:  'NoneType' object has no attribute 'hexewkb'
152/1190 adding/updating wdpa_pid 555706115 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 

196/1190 adding/updating wdpa_pid 555706159 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817486:  'NoneType' object has no attribute 'hexewkb'
197/1190 adding/updating wdpa_pid 555706160 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817487:  'NoneType' object has no attribute 'hexewkb'
198/1190 adding/updating wdpa_pid 555706161 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817488:  'NoneType' object has no attribute 'hexewkb'
199/1190 adding/updating wdpa_pid 555706162 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817489:  'NoneType' object has no attribute 'hexewkb'
200/1190 adding/updating wdpa_pid 555706163 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68817490:  'NoneType' object has no attribute 'hexewkb'
201/1190 adding/updating wdpa_pid 555706164 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 

...

1013/1190 adding/updating wdpa_pid 555706985 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818303:  'NoneType' object has no attribute 'hexewkb'
1014/1190 adding/updating wdpa_pid 555706986 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818304:  'NoneType' object has no attribute 'hexewkb'
1015/1190 adding/updating wdpa_pid 555706988 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818305:  'NoneType' object has no attribute 'hexewkb'
1016/1190 adding/updating wdpa_pid 555706989 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818306:  'NoneType' object has no attribute 'hexewkb'
1017/1190 adding/updating wdpa_pid 555706990 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818307:  'NoneType' object has no attribute 'hexewkb'
1018/1190 adding/updating wdpa_pid 555706991 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processin

1060/1190 adding/updating wdpa_pid 555707034 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818350:  'NoneType' object has no attribute 'hexewkb'
1061/1190 adding/updating wdpa_pid 555707035 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818351:  'NoneType' object has no attribute 'hexewkb'
1062/1190 adding/updating wdpa_pid 555707036 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818352:  'NoneType' object has no attribute 'hexewkb'
1063/1190 adding/updating wdpa_pid 555707037 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818353:  'NoneType' object has no attribute 'hexewkb'
1064/1190 adding/updating wdpa_pid 555707038 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818354:  'NoneType' object has no attribute 'hexewkb'
1065/1190 adding/updating wdpa_pid 555707039 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processin

1108/1190 adding/updating wdpa_pid 555707082 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818398:  'NoneType' object has no attribute 'hexewkb'
1109/1190 adding/updating wdpa_pid 555707083 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818399:  'NoneType' object has no attribute 'hexewkb'
1110/1190 adding/updating wdpa_pid 555707084 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818400:  'NoneType' object has no attribute 'hexewkb'
1111/1190 adding/updating wdpa_pid 555707085 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818401:  'NoneType' object has no attribute 'hexewkb'
1112/1190 adding/updating wdpa_pid 555707086 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818402:  'NoneType' object has no attribute 'hexewkb'
1113/1190 adding/updating wdpa_pid 555707087 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processin

1156/1190 adding/updating wdpa_pid 555707130 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818446:  'NoneType' object has no attribute 'hexewkb'
1157/1190 adding/updating wdpa_pid 555707131 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818447:  'NoneType' object has no attribute 'hexewkb'
1158/1190 adding/updating wdpa_pid 555707132 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818448:  'NoneType' object has no attribute 'hexewkb'
1159/1190 adding/updating wdpa_pid 555707133 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818449:  'NoneType' object has no attribute 'hexewkb'
1160/1190 adding/updating wdpa_pid 555707134 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processing mpa 68818450:  'NoneType' object has no attribute 'hexewkb'
1161/1190 adding/updating wdpa_pid 555707135 with mpa_id None
    Retained old MPAtlas values for: 
ERROR processin

True

In [60]:
# post_save.disconnect(mpa_post_save, sender=Mpa)
polys = WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2add).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=polys, poly=True, logfile=addpoly_log, geologfile=None, dryrun=False)
# post_save.connect(mpa_post_save, sender=Mpa)

1/970 adding/updating wdpa_pid 10098 with mpa_id 6031
    PID: 10098 has 17 field diffs 
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 6031: Access denied
2/970 adding/updating wdpa_pid 101165 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818481: Access denied
3/970 adding/updating wdpa_pid 101174 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818482: Access denied
4/970 adding/updating wdpa_pid 101734 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818483: Access denied
5/970 adding/updating wdpa_pid 102254 with mpa_id 2654
    PID: 102254 has 15 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 2654: Access denied
6/970 adding/updating wdpa_pid 109018 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_

Carto Error for mpa_id 68818496: Access denied
42/970 adding/updating wdpa_pid 24133_C with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818497: Access denied
43/970 adding/updating wdpa_pid 30023 with mpa_id 9771
    PID: 30023 has 18 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 9771: Access denied
44/970 adding/updating wdpa_pid 302129 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818498: Access denied
45/970 adding/updating wdpa_pid 302326_B with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818499: Access denied
46/970 adding/updating wdpa_pid 302950 with mpa_id 3749
    PID: 302950 has 8 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 3749: Access denied
47/970 adding/updating wdpa_pid 302976 with mpa_id

Carto Error for mpa_id 68818520: Access denied
86/970 adding/updating wdpa_pid 555516198 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818521: Access denied
87/970 adding/updating wdpa_pid 555516220 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818522: Access denied
88/970 adding/updating wdpa_pid 555516224 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818523: Access denied
89/970 adding/updating wdpa_pid 555516227 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818524: Access denied
90/970 adding/updating wdpa_pid 555516229 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818525: Access denied
91/970 adding/updating wdpa_pid 555516231 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818526: Access denied
92/970 adding/updating wdpa_pid 555516233 with mpa_id None
    Retained old MPAtlas value

Carto Error for mpa_id 68818555: Access denied
132/970 adding/updating wdpa_pid 555576213 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818556: Access denied
133/970 adding/updating wdpa_pid 555576383 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818557: Access denied
134/970 adding/updating wdpa_pid 555577385
 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818558: Access denied
135/970 adding/updating wdpa_pid 555586883 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818559: Access denied
136/970 adding/updating wdpa_pid 555592565 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818560: Access denied
137/970 adding/updating wdpa_pid 555593213 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818561: Access denied
138/970 adding/updating wdpa_pid 555593954 with mpa_id None
    Retained old MPAtl

Carto Error for mpa_id 68818607: Access denied
186/970 adding/updating wdpa_pid 555624868 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818608: Access denied
187/970 adding/updating wdpa_pid 555624869 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818609: Access denied
188/970 adding/updating wdpa_pid 555624870 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818610: Access denied
189/970 adding/updating wdpa_pid 555624871 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818611: Access denied
190/970 adding/updating wdpa_pid 555624872 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818612: Access denied
191/970 adding/updating wdpa_pid 555624873 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68818613: Access denied
192/970 adding/updating wdpa_pid 555624875 with mpa_id None
    Retained old MPAtla

...

Carto Error for mpa_id 68819225: Access denied
808/970 adding/updating wdpa_pid 555705702 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819226: Access denied
809/970 adding/updating wdpa_pid 555705703 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819227: Access denied
810/970 adding/updating wdpa_pid 555705704 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819228: Access denied
811/970 adding/updating wdpa_pid 555705705 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819229: Access denied
812/970 adding/updating wdpa_pid 555705708 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819230: Access denied
813/970 adding/updating wdpa_pid 555705710 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819231: Access denied
814/970 adding/updating wdpa_pid 555705714 with mpa_id None
    Retained old MPAtla

Carto Error for mpa_id 68819282: Access denied
865/970 adding/updating wdpa_pid 555708862 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819283: Access denied
866/970 adding/updating wdpa_pid 555708867 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819284: Access denied
867/970 adding/updating wdpa_pid 555708964 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819285: Access denied
868/970 adding/updating wdpa_pid 555708983 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819286: Access denied
869/970 adding/updating wdpa_pid 555709046 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819287: Access denied
870/970 adding/updating wdpa_pid 555709050 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819288: Access denied
871/970 adding/updating wdpa_pid 555709062 with mpa_id None
    Retained old MPAtla

Carto Error for mpa_id 68819339: Access denied
922/970 adding/updating wdpa_pid 555712540 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819340: Access denied
923/970 adding/updating wdpa_pid 555712544 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819341: Access denied
924/970 adding/updating wdpa_pid 555712556 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819342: Access denied
925/970 adding/updating wdpa_pid 555712665 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819343: Access denied
926/970 adding/updating wdpa_pid 555712717 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819344: Access denied
927/970 adding/updating wdpa_pid 555712825 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819345: Access denied
928/970 adding/updating wdpa_pid 555712984 with mpa_id None
    Retained old MPAtla

    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 7399: Access denied
971/970 adding/updating wdpa_pid 902851 with mpa_id 7434
    PID: 902851 has 11 field diffs 
    MPAtlas orig geom area is zero, using WDPA boundaries
    Retained old MPAtlas values for: 
Carto Error for mpa_id 7434: Access denied
972/970 adding/updating wdpa_pid 9035_B with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819376: Access denied
973/970 adding/updating wdpa_pid 9628 with mpa_id None
    Retained old MPAtlas values for: 
Carto Error for mpa_id 68819377: Access denied


True

In [112]:
bad = WdpaPoly_new.objects.get(wdpa_pid='555643543')
bg = bad.geom
bg.num_coords

bad = WdpaPoly_new.objects.get(wdpa_pid='555643544')
bg = bad.geom
bg.num_coords

2833099

In [61]:
reload(merge)
updatepoint_geolog = logprefix + 'updatepoint_noUSA_noCHL_2020_log.json'
updatepoly_log = logprefix + 'updatepoly_noUSA_noCHL_2020_log.json'
updatepoly_geolog = logprefix + 'updatepoly_noUSA_noCHL_2020_geo_log.json'
# updatepoint_geolog = '/Users/russmo/Code/wdpa/log/updatepoint_TUV_2010_v3_geo_log.json'
# updatepoly_log = '/Users/russmo/Code/wdpa/log/updatepoly_TUV_2019_v3_log.json'
# updatepoly_geolog = '/Users/russmo/Code/wdpa/log/updatepoly_TUV_2019_v3_geo_log.json'

In [62]:
# wdpa_filter = (
# #     Q(iso3__icontains='USA') | Q(parent_iso3__icontains='USA') |
# #     Q(iso3__icontains='UMI') | Q(parent_iso3__icontains='UMI') |
# #     Q(iso3__icontains='VIR') | Q(parent_iso3__icontains='VIR') |
# #     Q(iso3__icontains='PRI') | Q(parent_iso3__icontains='PRI') |
# #     Q(iso3__icontains='ASM') | Q(parent_iso3__icontains='ASM') |
# #     Q(iso3__icontains='GUM') | Q(parent_iso3__icontains='GUM') |
# #     Q(iso3__icontains='MNP') | Q(parent_iso3__icontains='MNP') |
#     Q(iso3__icontains='MEX') | Q(iso3__icontains='CHL') | Q(iso3__icontains='IDN') | 
#     Q(iso3__icontains='CHN') | Q(iso3__icontains='JPN') | 
#     Q(parent_iso3__icontains='MEX') | Q(parent_iso3__icontains='CHL') | Q(parent_iso3__icontains='IDN') |
#     Q(parent_iso3__icontains='CHN') | Q(parent_iso3__icontains='JPN') #|
# #     Q(iso3__icontains='FRA') | Q(parent_iso3__icontains='FRA') |
# #     Q(iso3__icontains='ATF') | Q(iso3__icontains='BLM') | Q(iso3__icontains='GLP') |
# #     Q(iso3__icontains='GUF') | Q(iso3__icontains='MAF') | Q(iso3__icontains='MTQ') |
# #     Q(iso3__icontains='MYT') | Q(iso3__icontains='NCL') | Q(iso3__icontains='PYF') |
# #     Q(iso3__icontains='REU') | Q(iso3__icontains='SHN') | Q(iso3__icontains='SYC') |
# #     Q(iso3__icontains='AUS') | Q(parent_iso3__icontains='AUS') |
# #     Q(iso3__icontains='ZAF') | Q(parent_iso3__icontains='ZAF') |
# #     Q(iso3__icontains='CAN') | Q(parent_iso3__icontains='CAN') |
# #     Q(iso3__icontains='GBR') | Q(parent_iso3__icontains='GBR') |
# #     Q(iso3__icontains='AIA') | Q(iso3__icontains='BMU') | Q(iso3__icontains='CYM') |
# #     Q(iso3__icontains='FLK') | Q(iso3__icontains='GIB') | Q(iso3__icontains='IMN') |
# #     Q(iso3__icontains='IOT') | Q(iso3__icontains='JEY') | Q(iso3__icontains='MSR') |
# #     Q(iso3__icontains='PCN') | Q(iso3__icontains='SGS') | Q(iso3__icontains='SHN') |
# #     Q(iso3__icontains='TCA') | Q(iso3__icontains='VGB')
# )
wdpa_filter = (
    Q()
)

wdpa_exclude = (
    Q(iso3__icontains='USA') | Q(parent_iso3__icontains='USA') |
    Q(iso3__icontains='UMI') | Q(parent_iso3__icontains='UMI') |
    Q(iso3__icontains='VIR') | Q(parent_iso3__icontains='VIR') |
    Q(iso3__icontains='PRI') | Q(parent_iso3__icontains='PRI') |
    Q(iso3__icontains='ASM') | Q(parent_iso3__icontains='ASM') |
    Q(iso3__icontains='GUM') | Q(parent_iso3__icontains='GUM') |
    Q(iso3__icontains='MNP') | Q(parent_iso3__icontains='MNP') |
    Q(iso3__icontains='CHL') | Q(parent_iso3__icontains='CHL')
#     Q(iso3__icontains='MEX') | Q(iso3__icontains='CHL') | Q(iso3__icontains='IDN') | 
#     Q(iso3__icontains='CHN') | Q(iso3__icontains='JPN') | 
#     Q(parent_iso3__icontains='MEX') | Q(parent_iso3__icontains='CHL') | Q(parent_iso3__icontains='IDN') |
#     Q(parent_iso3__icontains='CHN') | Q(parent_iso3__icontains='JPN')
)
polys = WdpaPoly_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('1','2')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
points = WdpaPoint_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('1','2')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
allpid2update = list(set(list(polys) + list(points)))

polys_nonmarine = WdpaPoly_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('0')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
points_nonmarine = WdpaPoint_new.objects.exclude(wdpa_pid__in=allpid2add).exclude(wdpa_exclude).filter(wdpa_filter).filter(marine__in=('0')).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)
allpid2update_nonmarine = list(set(list(polys_nonmarine) + list(points_nonmarine)))

allpid2update_nonmarine_inmpatlas = mpaset.filter(wdpa_pid__in=allpid2update_nonmarine).order_by('wdpa_pid').values_list('wdpa_pid', flat=True)

allpid2update_marine012 = allpid2update + list(allpid2update_nonmarine_inmpatlas)

In [63]:
print('marine:', len(allpid2update), 'nonmarine:', len(allpid2update_nonmarine), 'all:', len(allpid2update_marine012))
print('POINTS --', 
      'marine:', WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2update_nonmarine).count()
)
print('POLYGONS --', 
      'marine:', WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2update_nonmarine).count(),
)
print('MPATLAS Records --', 
      'marine:', mpaset.filter(wdpa_pid__in=allpid2update).count(),
      'nonmarine:', mpaset.filter(wdpa_pid__in=allpid2update_nonmarine).count(),
)

marine: 15505 nonmarine: 204356 all: 19076
POINTS -- marine: 492 nonmarine: 10783
POLYGONS -- marine: 15013 nonmarine: 193573
MPATLAS Records -- marine: 15806 nonmarine: 3571


In [64]:
len(set(allpid2update_marine012))

18926

In [65]:
# All marine=1,2 sites and only marine=0 that exist in MPAtlas
updatepoints = WdpaPoint_new.objects.filter(wdpa_pid__in=allpid2update_marine012).order_by('wdpa_pid')
merge.updateMpasFromWdpaQueryset(qs=updatepoints, poly=False, logfile=None, geologfile=updatepoint_geolog, dryrun=False)

1/869 adding/updating wdpa_pid 10093 with mpa_id 6028
    PID: 10093 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6028:  'NoneType' object has no attribute 'hexewkb'
2/869 adding/updating wdpa_pid 10170 with mpa_id 6032
    PID: 10170 has 5 field diffs 
    Retained old MPAtlas values for: name designation designation_eng
ERROR processing mpa 6032:  'NoneType' object has no attribute 'hexewkb'
3/869 adding/updating wdpa_pid 101838 with mpa_id 68813475
    PID: 101838 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68813475:  'NoneType' object has no attribute 'hexewkb'
4/869 adding/updating wdpa_pid 10720 with mpa_id 6037
    PID: 10720 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6037:  'NoneType' object has no attribute 'hexewkb'
5/869 adding/updating wdpa_pid 10724 with mpa_id 6039
    PID: 10724 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6039:  'NoneTyp

    Retained old MPAtlas values for: 
ERROR processing mpa 6163:  'NoneType' object has no attribute 'hexewkb'
42/869 adding/updating wdpa_pid 13200 with mpa_id 6164
    PID: 13200 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6164:  'NoneType' object has no attribute 'hexewkb'
43/869 adding/updating wdpa_pid 13201 with mpa_id 6165
    PID: 13201 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6165:  'NoneType' object has no attribute 'hexewkb'
44/869 adding/updating wdpa_pid 13202 with mpa_id 6166
    PID: 13202 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6166:  'NoneType' object has no attribute 'hexewkb'
45/869 adding/updating wdpa_pid 13203 with mpa_id 6167
    PID: 13203 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6167:  'NoneType' object has no attribute 'hexewkb'
46/869 adding/updating wdpa_pid 13205 with mpa_id 6168
    PID: 13205 has 2 field diffs 


    Retained old MPAtlas values for: 
ERROR processing mpa 6204:  'NoneType' object has no attribute 'hexewkb'
83/869 adding/updating wdpa_pid 13243 with mpa_id 6205
    PID: 13243 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6205:  'NoneType' object has no attribute 'hexewkb'
84/869 adding/updating wdpa_pid 13244 with mpa_id 6206
    PID: 13244 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6206:  'NoneType' object has no attribute 'hexewkb'
85/869 adding/updating wdpa_pid 13245 with mpa_id 6207
    PID: 13245 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6207:  'NoneType' object has no attribute 'hexewkb'
86/869 adding/updating wdpa_pid 13246 with mpa_id 6208
    PID: 13246 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6208:  'NoneType' object has no attribute 'hexewkb'
87/869 adding/updating wdpa_pid 13247 with mpa_id 6209
    PID: 13247 has 2 field diffs 


124/869 adding/updating wdpa_pid 14255 with mpa_id 6318
    PID: 14255 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6318:  'NoneType' object has no attribute 'hexewkb'
125/869 adding/updating wdpa_pid 14256 with mpa_id 6319
    PID: 14256 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6319:  'NoneType' object has no attribute 'hexewkb'
126/869 adding/updating wdpa_pid 14257 with mpa_id 6320
    PID: 14257 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6320:  'NoneType' object has no attribute 'hexewkb'
127/869 adding/updating wdpa_pid 14258 with mpa_id 6321
    PID: 14258 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6321:  'NoneType' object has no attribute 'hexewkb'
128/869 adding/updating wdpa_pid 14261 with mpa_id 6322
    PID: 14261 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6322:  'NoneType' object has no attribute 'hexe

    Retained old MPAtlas values for: 
ERROR processing mpa 68813503:  'NoneType' object has no attribute 'hexewkb'
163/869 adding/updating wdpa_pid 154001 with mpa_id 68813504
    PID: 154001 has 3 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68813504:  'NoneType' object has no attribute 'hexewkb'
164/869 adding/updating wdpa_pid 154015 with mpa_id 68813505
    PID: 154015 has 4 field diffs  and GEOM diff
    Retained old MPAtlas values for: 
ERROR processing mpa 68813505:  'NoneType' object has no attribute 'hexewkb'
165/869 adding/updating wdpa_pid 154072 with mpa_id 68813506
    PID: 154072 has 4 field diffs  and GEOM diff
    Retained old MPAtlas values for: 
ERROR processing mpa 68813506:  'NoneType' object has no attribute 'hexewkb'
166/869 adding/updating wdpa_pid 154468 with mpa_id 68813507
    PID: 154468 has 4 field diffs  and GEOM diff
    Retained old MPAtlas values for: 
ERROR processing mpa 68813507:  'NoneType' object has no attribute 'hexewkb'

...

714/869 adding/updating wdpa_pid 555621417 with mpa_id 68808486
    PID: 555621417 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68808486:  'NoneType' object has no attribute 'hexewkb'
715/869 adding/updating wdpa_pid 555621418 with mpa_id 68808487
    PID: 555621418 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68808487:  'NoneType' object has no attribute 'hexewkb'
716/869 adding/updating wdpa_pid 555621419 with mpa_id 68808488
    PID: 555621419 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68808488:  'NoneType' object has no attribute 'hexewkb'
717/869 adding/updating wdpa_pid 555621420 with mpa_id 68808489
    PID: 555621420 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68808489:  'NoneType' object has no attribute 'hexewkb'
718/869 adding/updating wdpa_pid 555621421 with mpa_id 68808490
    PID: 555621421 has 2 field diffs 
    Retained old MPAtlas value

    Retained old MPAtlas values for: 
ERROR processing mpa 68810707:  'NoneType' object has no attribute 'hexewkb'
752/869 adding/updating wdpa_pid 555636357 with mpa_id 68810708
    PID: 555636357 has 3 field diffs  and GEOM diff
    Retained old MPAtlas values for: 
ERROR processing mpa 68810708:  'NoneType' object has no attribute 'hexewkb'
753/869 adding/updating wdpa_pid 555643547 with mpa_id 68813671
    PID: 555643547 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 68813671:  'NoneType' object has no attribute 'hexewkb'
754/869 adding/updating wdpa_pid 61523 with mpa_id 6647
    PID: 61523 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6647:  'NoneType' object has no attribute 'hexewkb'
755/869 adding/updating wdpa_pid 61525 with mpa_id 6648
    PID: 61525 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 6648:  'NoneType' object has no attribute 'hexewkb'
756/869 adding/updating wdpa_pid 61

792/869 adding/updating wdpa_pid 900593 with mpa_id 7274
    PID: 900593 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7274:  'NoneType' object has no attribute 'hexewkb'
793/869 adding/updating wdpa_pid 900595 with mpa_id 7275
    PID: 900595 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7275:  'NoneType' object has no attribute 'hexewkb'
794/869 adding/updating wdpa_pid 900602 with mpa_id 7277
    PID: 900602 has 3 field diffs  and GEOM diff
    Retained old MPAtlas values for: 
ERROR processing mpa 7277:  'NoneType' object has no attribute 'hexewkb'
795/869 adding/updating wdpa_pid 900604 with mpa_id 7278
    PID: 900604 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7278:  'NoneType' object has no attribute 'hexewkb'
796/869 adding/updating wdpa_pid 900605 with mpa_id 7279
    PID: 900605 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7279:  'NoneType' objec

832/869 adding/updating wdpa_pid 902377 with mpa_id 7376
    PID: 902377 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7376:  'NoneType' object has no attribute 'hexewkb'
833/869 adding/updating wdpa_pid 902505 with mpa_id 7707385
    PID: 902505 has 4 field diffs 
    Retained old MPAtlas values for: no_take no_take_area
ERROR processing mpa 7707385:  'NoneType' object has no attribute 'hexewkb'
834/869 adding/updating wdpa_pid 902505 with mpa_id 7385
    PID: 902505 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7385:  'NoneType' object has no attribute 'hexewkb'
835/869 adding/updating wdpa_pid 902511 with mpa_id 7386
    PID: 902511 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 7386:  'NoneType' object has no attribute 'hexewkb'
836/869 adding/updating wdpa_pid 902536 with mpa_id 9482
    PID: 902536 has 2 field diffs 
    Retained old MPAtlas values for: 
ERROR processing mpa 9482:  'Non

True

In [28]:
# Chilean site Kawésqar has a feature geometry with about 3936041 vertices
# It swamps the geodatabase and GeoDjango on feature save postprocessing and other tasks
# Use this previously simplified feature instead
kawesqar_wdpa_pid = 555643543
kawesqar_mpa_id = 68813461
kw = WdpaPoly_new.objects.get(wdpa_pid=kawesqar_wdpa_pid)
kw_old = WdpaPoly_prev.objects.get(wdpa_pid=kawesqar_wdpa_pid)
km = Mpa.objects.get(mpa_id=kawesqar_mpa_id)
print(kw.geom.num_coords, kw_old.geom.num_coords, km.geom.num_coords)
kw_geom = kw.geom.clone()
kw.geom = km.geom
kw_old.geom = km.geom
kw.save()
kw_old.save()
print(kw.geom.num_coords, kw_old.geom.num_coords, km.geom.num_coords)
print(km.name, km.designation)

288829 288829 288829
288829 288829 288829
Kawésqar Parque Nacional


In [27]:
chl2_wdpa_pid = 555643544
chl2_mpa_id = 68813462
cw = WdpaPoly_new.objects.get(wdpa_pid=chl2_wdpa_pid)
cw_old = WdpaPoly_prev.objects.get(wdpa_pid=chl2_wdpa_pid)
cm = Mpa.objects.get(mpa_id=chl2_mpa_id)
print(cw.geom.num_coords, cw_old.geom.num_coords, cm.geom.num_coords)
cm.name, cm.designation

2833099 2833100 296451


('Kawésqar', 'Reserva Nacional')

In [66]:
reload(merge)
# All marine=1,2 sites and only marine=0 that exist in MPAtlas
updatepolys = WdpaPoly_new.objects.filter(wdpa_pid__in=allpid2update_marine012).order_by('wdpa_pid')
#updatepolys = updatepolys.exclude(wdpa_pid__in=partialrunids)
merge.updateMpasFromWdpaQueryset(qs=updatepolys, poly=True, logfile=updatepoly_log, geologfile=None, dryrun=True)

1/18508 adding/updating wdpa_pid 1 with mpa_id 1
    PID: 1 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
2/18508 adding/updating wdpa_pid 1 with mpa_id 67700001
    PID: 1 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
3/18508 adding/updating wdpa_pid 100024 with mpa_id 6805
    PID: 100024 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
4/18508 adding/updating wdpa_pid 10028 with mpa_id 787
    PID: 10028 has 14 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
5/18508 adding/updating wdpa_pid 10072 with mpa_id 788
    PID: 10072 has 16 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
6/18508 adding/updating wdpa_pid 10083

    PID: 101768 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
51/18508 adding/updating wdpa_pid 101769 with mpa_id 6809
    PID: 101769 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
52/18508 adding/updating wdpa_pid 101774 with mpa_id 6810
    PID: 101774 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
53/18508 adding/updating wdpa_pid 101775 with mpa_id 6811
    PID: 101775 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
54/18508 adding/updating wdpa_pid 101777 with mpa_id 6812
    PID: 101777 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
55/18508 adding/updating wdpa_pid 101778 with mpa_id 6813
    PID: 1

91/18508 adding/updating wdpa_pid 102322 with mpa_id 67702659
    PID: 102322 has 8 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
92/18508 adding/updating wdpa_pid 102328 with mpa_id 68810725
    PID: 102328 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
93/18508 adding/updating wdpa_pid 102332 with mpa_id 2660
    PID: 102332 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
94/18508 adding/updating wdpa_pid 102357 with mpa_id 2661
    PID: 102357 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
95/18508 adding/updating wdpa_pid 102367 with mpa_id 2662
    PID: 102367 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
96

129/18508 adding/updating wdpa_pid 103383 with mpa_id 2690
    PID: 103383 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
130/18508 adding/updating wdpa_pid 10339 with mpa_id 9736
    PID: 10339 has 2 field diffs 
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
131/18508 adding/updating wdpa_pid 103394 with mpa_id 2691
    PID: 103394 has 5 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
132/18508 adding/updating wdpa_pid 103396 with mpa_id 2692
    PID: 103396 has 5 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
133/18508 adding/updating wdpa_pid 10340 with mpa_id 797
    PID: 10340 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
134/18508 adding/updatin

171/18508 adding/updating wdpa_pid 10460 with mpa_id 821
    PID: 10460 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take
172/18508 adding/updating wdpa_pid 10461 with mpa_id 68813679
    PID: 10461 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
173/18508 adding/updating wdpa_pid 10462 with mpa_id 822
    PID: 10462 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
174/18508 adding/updating wdpa_pid 10465 with mpa_id 823
    PID: 10465 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
175/18508 adding/updating wdpa_pid 10466 with mpa_id 824
    PID: 10466 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take
1

...

    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18532/18508 adding/updating wdpa_pid 941 with mpa_id 141
    PID: 941 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18533/18508 adding/updating wdpa_pid 9413 with mpa_id 749
    PID: 9413 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18534/18508 adding/updating wdpa_pid 942 with mpa_id 142
    PID: 942 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18535/18508 adding/updating wdpa_pid 9465 with mpa_id 750
    PID: 9465 has 14 field diffs  and GEOM diff
    Geom areas 0.3927350266836697% dissimilar, keeping existing MPAtlas boundaries
    Retained old MPAtlas values for: status_year rep_m_area rep_area calc_area calc_m_area no_take no_take_area marine own_type mgmt_aut

    PID: 95308 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18572/18508 adding/updating wdpa_pid 95310 with mpa_id 2533
    PID: 95310 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18573/18508 adding/updating wdpa_pid 95310 with mpa_id 7702533
    PID: 95310 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18574/18508 adding/updating wdpa_pid 95315 with mpa_id 2534
    PID: 95315 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18575/18508 adding/updating wdpa_pid 95317 with mpa_id 6777
    PID: 95317 has 7 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18576/18508 adding/updating wdpa_pid 95317 with mpa_id 7706777

    PID: 9637 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18613/18508 adding/updating wdpa_pid 9637 with mpa_id 7700754
    PID: 9637 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18614/18508 adding/updating wdpa_pid 967 with mpa_id 146
    PID: 967 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18615/18508 adding/updating wdpa_pid 968 with mpa_id 147
    PID: 968 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18616/18508 adding/updating wdpa_pid 9712 with mpa_id 755
    PID: 9712 has 3 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18617/18508 adding/updating wdpa_pid 9712 with mpa_id 67700755
    PID: 9712 h

18654/18508 adding/updating wdpa_pid 9910 with mpa_id 777
    PID: 9910 has 5 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18655/18508 adding/updating wdpa_pid 9915 with mpa_id 778
    PID: 9915 has 5 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18656/18508 adding/updating wdpa_pid 9920 with mpa_id 779
    PID: 9920 has 4 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: 
18657/18508 adding/updating wdpa_pid 9922 with mpa_id 780
    PID: 9922 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for: no_take marine own_type
18658/18508 adding/updating wdpa_pid 9924 with mpa_id 781
    PID: 9924 has 6 field diffs  and GEOM diff
    Geom areas similar (0.0%), using WDPA boundaries
    Retained old MPAtlas values for

True

In [68]:
mpids = mpaset.filter(wdpa_id__isnull=False, wdpa_pid__isnull=False)
mpids_count = mpids.count()
count = 0
for m in mpids:
    count += 1
    try:
        w = WdpaPoly_new.objects.filter(wdpa_pid=m.wdpa_pid)
    except:
        try:
            w = WdpaPoint_new.objects.filter(wdpa_pid=m.wdpa_pid)
        except:
            pass
    if w.exists():
        w0 = w[0]
        mq = mpaset.filter(pk=m.pk)
        print('%s/%s mpa_id %s wdpa_pid %s updated with _wdpa values' % (count, mpids_count, m.mpa_id, w0.wdpa_pid))
        mq.update(
            no_take_wdpa=w0.no_take,
            no_take_area_wdpa=w0.no_tk_area,
        )

1/22622 mpa_id 68815627 wdpa_pid 555515656 updated with _wdpa values
2/22622 mpa_id 68814918 wdpa_pid 31183 updated with _wdpa values
3/22622 mpa_id 786 wdpa_pid 9991 updated with _wdpa values
4/22622 mpa_id 68814876 wdpa_pid 311035 updated with _wdpa values
5/22622 mpa_id 68814873 wdpa_pid 311025 updated with _wdpa values
6/22622 mpa_id 68812005 wdpa_pid 555541494 updated with _wdpa values
7/22622 mpa_id 68814893 wdpa_pid 311246 updated with _wdpa values
8/22622 mpa_id 68814896 wdpa_pid 311303 updated with _wdpa values
9/22622 mpa_id 68816987 wdpa_pid 555643120 updated with _wdpa values
11/22622 mpa_id 68814904 wdpa_pid 311616 updated with _wdpa values
12/22622 mpa_id 68814908 wdpa_pid 311635 updated with _wdpa values
13/22622 mpa_id 68814272 wdpa_pid 170115 updated with _wdpa values
14/22622 mpa_id 68814906 wdpa_pid 311618 updated with _wdpa values
15/22622 mpa_id 68814920 wdpa_pid 312629 updated with _wdpa values
16/22622 mpa_id 68816717 wdpa_pid 555624850 updated with _wdpa values


133/22622 mpa_id 2539 wdpa_pid 95339 updated with _wdpa values
134/22622 mpa_id 1620 wdpa_pid 24377 updated with _wdpa values
136/22622 mpa_id 12794 wdpa_pid 555526169 updated with _wdpa values
137/22622 mpa_id 68810377 wdpa_pid 555581099 updated with _wdpa values
138/22622 mpa_id 861 wdpa_pid 10948 updated with _wdpa values
139/22622 mpa_id 15911 wdpa_pid 555579282 updated with _wdpa values
140/22622 mpa_id 68810378 wdpa_pid 555581100 updated with _wdpa values
141/22622 mpa_id 68813404 wdpa_pid 555573987 updated with _wdpa values
142/22622 mpa_id 865 wdpa_pid 10984 updated with _wdpa values
143/22622 mpa_id 14773 wdpa_pid 555549242 updated with _wdpa values
144/22622 mpa_id 14766 wdpa_pid 555549235 updated with _wdpa values
145/22622 mpa_id 3966 wdpa_pid 305818 updated with _wdpa values
146/22622 mpa_id 14769 wdpa_pid 555549238 updated with _wdpa values
147/22622 mpa_id 68810510 wdpa_pid 555583028 updated with _wdpa values
148/22622 mpa_id 12636 wdpa_pid 555523034 updated with _wdpa v

264/22622 mpa_id 68815452 wdpa_pid 392092 updated with _wdpa values
265/22622 mpa_id 68812203 wdpa_pid 555558350 updated with _wdpa values
266/22622 mpa_id 12175 wdpa_pid 396543 updated with _wdpa values
267/22622 mpa_id 3970 wdpa_pid 305833 updated with _wdpa values
268/22622 mpa_id 68813808 wdpa_pid 136071 updated with _wdpa values
269/22622 mpa_id 13002 wdpa_pid 555528015 updated with _wdpa values
270/22622 mpa_id 5775 wdpa_pid 555528032 updated with _wdpa values
271/22622 mpa_id 7703887 wdpa_pid 305369 updated with _wdpa values
272/22622 mpa_id 68813817 wdpa_pid 136136 updated with _wdpa values
273/22622 mpa_id 68813821 wdpa_pid 136173 updated with _wdpa values
274/22622 mpa_id 7703888 wdpa_pid 305372 updated with _wdpa values
275/22622 mpa_id 68813820 wdpa_pid 136165 updated with _wdpa values
276/22622 mpa_id 68815462 wdpa_pid 392110 updated with _wdpa values
277/22622 mpa_id 68808559 wdpa_pid 555621387 updated with _wdpa values
278/22622 mpa_id 68813822 wdpa_pid 136175 updated wi

391/22622 mpa_id 68811314 wdpa_pid 555514086 updated with _wdpa values
393/22622 mpa_id 68810017 wdpa_pid 555541739 updated with _wdpa values
394/22622 mpa_id 68813019 wdpa_pid 555623692 updated with _wdpa values
395/22622 mpa_id 68810447 wdpa_pid 555581579 updated with _wdpa values
396/22622 mpa_id 13079 wdpa_pid 555529065 updated with _wdpa values
397/22622 mpa_id 68809667 wdpa_pid 135898 updated with _wdpa values
398/22622 mpa_id 3087 wdpa_pid 152292 updated with _wdpa values
399/22622 mpa_id 503 wdpa_pid 4870 updated with _wdpa values
400/22622 mpa_id 68816418 wdpa_pid 555588191 updated with _wdpa values
401/22622 mpa_id 68810443 wdpa_pid 555581547 updated with _wdpa values
402/22622 mpa_id 68810445 wdpa_pid 555581557 updated with _wdpa values
403/22622 mpa_id 68810438 wdpa_pid 555581521 updated with _wdpa values
404/22622 mpa_id 5246 wdpa_pid 478040 updated with _wdpa values
405/22622 mpa_id 68814717 wdpa_pid 305597 updated with _wdpa values
406/22622 mpa_id 3952 wdpa_pid 305791 u

516/22622 mpa_id 68815802 wdpa_pid 555540235 updated with _wdpa values
517/22622 mpa_id 11809 wdpa_pid 388307 updated with _wdpa values
518/22622 mpa_id 3914 wdpa_pid 305525 updated with _wdpa values
519/22622 mpa_id 11805 wdpa_pid 388302 updated with _wdpa values
520/22622 mpa_id 3921 wdpa_pid 305591 updated with _wdpa values
521/22622 mpa_id 11804 wdpa_pid 388301 updated with _wdpa values
522/22622 mpa_id 13436 wdpa_pid 555534177 updated with _wdpa values
523/22622 mpa_id 68814810 wdpa_pid 308059 updated with _wdpa values
524/22622 mpa_id 3922 wdpa_pid 305593 updated with _wdpa values
525/22622 mpa_id 68812812 wdpa_pid 555600202 updated with _wdpa values
526/22622 mpa_id 7005 wdpa_pid 305610 updated with _wdpa values
527/22622 mpa_id 15731 wdpa_pid 555578634 updated with _wdpa values
528/22622 mpa_id 68812816 wdpa_pid 555600266 updated with _wdpa values
529/22622 mpa_id 7006 wdpa_pid 305621 updated with _wdpa values
530/22622 mpa_id 68810063 wdpa_pid 555541851 updated with _wdpa valu

...

4836/22622 mpa_id 4797 wdpa_pid 315024 updated with _wdpa values
4837/22622 mpa_id 13888 wdpa_pid 555540592 updated with _wdpa values
4838/22622 mpa_id 68815682 wdpa_pid 555538332 updated with _wdpa values
4839/22622 mpa_id 12617 wdpa_pid 555522629 updated with _wdpa values
4840/22622 mpa_id 12619 wdpa_pid 555522639 updated with _wdpa values
4841/22622 mpa_id 68810100 wdpa_pid 555556943 updated with _wdpa values
4842/22622 mpa_id 11976 wdpa_pid 391677 updated with _wdpa values
4843/22622 mpa_id 68812757 wdpa_pid 555593077 updated with _wdpa values
4844/22622 mpa_id 13527 wdpa_pid 555537248 updated with _wdpa values
4845/22622 mpa_id 67700243 wdpa_pid 1937 updated with _wdpa values
4846/22622 mpa_id 68812889 wdpa_pid 555622178 updated with _wdpa values
4847/22622 mpa_id 2773 wdpa_pid 126763 updated with _wdpa values
4848/22622 mpa_id 10182 wdpa_pid 155195 updated with _wdpa values
4849/22622 mpa_id 68815466 wdpa_pid 392126 updated with _wdpa values
4850/22622 mpa_id 1658 wdpa_pid 26012 

4957/22622 mpa_id 153 wdpa_pid 1058 updated with _wdpa values
4958/22622 mpa_id 1371 wdpa_pid 18282 updated with _wdpa values
4959/22622 mpa_id 3455 wdpa_pid 183119 updated with _wdpa values
4960/22622 mpa_id 15242 wdpa_pid 555567625 updated with _wdpa values
4961/22622 mpa_id 68810109 wdpa_pid 555556952 updated with _wdpa values
4962/22622 mpa_id 3534 wdpa_pid 198430 updated with _wdpa values
4963/22622 mpa_id 2326 wdpa_pid 68148 updated with _wdpa values
4964/22622 mpa_id 12625 wdpa_pid 555522749 updated with _wdpa values
4966/22622 mpa_id 68812909 wdpa_pid 555622206 updated with _wdpa values
4967/22622 mpa_id 5614 wdpa_pid 555512429 updated with _wdpa values
4968/22622 mpa_id 1836 wdpa_pid 32615 updated with _wdpa values
4969/22622 mpa_id 9911 wdpa_pid 147553 updated with _wdpa values
4970/22622 mpa_id 5616 wdpa_pid 555512431 updated with _wdpa values
4971/22622 mpa_id 68812910 wdpa_pid 555622209 updated with _wdpa values
4972/22622 mpa_id 5615 wdpa_pid 555512430 updated with _wdpa 

5081/22622 mpa_id 12634 wdpa_pid 555523032 updated with _wdpa values
5082/22622 mpa_id 4829 wdpa_pid 315480 updated with _wdpa values
5083/22622 mpa_id 12635 wdpa_pid 555523033 updated with _wdpa values
5084/22622 mpa_id 68813263 wdpa_pid 68162 updated with _wdpa values
5085/22622 mpa_id 68811924 wdpa_pid 555540807 updated with _wdpa values
5086/22622 mpa_id 12640 wdpa_pid 555523038 updated with _wdpa values
5087/22622 mpa_id 2709 wdpa_pid 106787 updated with _wdpa values
5088/22622 mpa_id 12420 wdpa_pid 555512476 updated with _wdpa values
5089/22622 mpa_id 12661 wdpa_pid 555523679 updated with _wdpa values
5090/22622 mpa_id 68812932 wdpa_pid 555622285 updated with _wdpa values
5091/22622 mpa_id 5653 wdpa_pid 555512481 updated with _wdpa values
5092/22622 mpa_id 13905 wdpa_pid 555540811 updated with _wdpa values
5093/22622 mpa_id 5392 wdpa_pid 555511965 updated with _wdpa values
5094/22622 mpa_id 2332 wdpa_pid 68168 updated with _wdpa values
5095/22622 mpa_id 10961 wdpa_pid 183041 upda

5205/22622 mpa_id 4835 wdpa_pid 315486 updated with _wdpa values
5206/22622 mpa_id 68809909 wdpa_pid 555535775 updated with _wdpa values
5207/22622 mpa_id 11003 wdpa_pid 183219 updated with _wdpa values
5208/22622 mpa_id 11545 wdpa_pid 345589 updated with _wdpa values
5209/22622 mpa_id 68811947 wdpa_pid 555541062 updated with _wdpa values
5210/22622 mpa_id 12669 wdpa_pid 555523703 updated with _wdpa values
5211/22622 mpa_id 68809870 wdpa_pid 174703 updated with _wdpa values
5212/22622 mpa_id 68809913 wdpa_pid 555535782 updated with _wdpa values
5213/22622 mpa_id 12490 wdpa_pid 555517871 updated with _wdpa values
5214/22622 mpa_id 14421 wdpa_pid 555547772 updated with _wdpa values
5215/22622 mpa_id 11009 wdpa_pid 183225 updated with _wdpa values
5216/22622 mpa_id 4836 wdpa_pid 315487 updated with _wdpa values
5217/22622 mpa_id 15979 wdpa_pid 555579739 updated with _wdpa values
5218/22622 mpa_id 68812953 wdpa_pid 555622365 updated with _wdpa values
5219/22622 mpa_id 68810125 wdpa_pid 555

InternalError: could not open file "base/4182909/4877302_fsm": Interrupted system call
CONTEXT:  writing block 2 of relation base/4182909/4877302_fsm


mpaset.filter(wdpa_pid__isnull=False).update(
    no_take_wdpa=F('no_take'), no_take_area_wdpa=F('no_take_area')
)

In [ ]:
nt = ('All', 'Part', 'None')
ntupdate = mpaset.filter(wdpa_pid__isnull=False).filter(
    (~Q(no_take_wdpa__in=('All')) & Q(no_take_mpatlas__in=('All')))
    | (~Q(no_take_wdpa__in=('All', 'Part')) & Q(no_take_mpatlas__in=('All', 'Part')))
    | (Q(no_take_wdpa__in=('Not Applicable')) & Q(no_take_mpatlas__in=('All', 'Part', 'None')))
)
ntupdate.update(no_take=F('no_take_mpatlas'))

In [ ]:
ntareaupdate = mpaset.filter(wdpa_pid__isnull=False).filter(
    Q(no_take_area_mpatlas__isnull=False) &
    (
        Q(no_take_area_wdpa__isnull=True)
        | Q(no_take_area_mpatlas__gt=F('no_take_area_wdpa'))
    )
)
ntareaupdate.update(no_take_area=F('no_take_area_mpatlas'))

In [ ]:
ntchanges = ntupdate | ntareaupdate
for n in ntchanges:
    print(n.mpa_id, n.wdpa_id, n.wdpa_pid, n.name, n.designation, n.designation_eng, n.no_take_wdpa, n.no_take_mpatlas, n.no_take_area_wdpa, n.no_take_area_mpatlas)

In [ ]:
ntchanges = ntupdate | ntareaupdate

import csv

nt_log = logprefix + 'notakechange_noUSA_noCHL_log.csv'
with open(nt_log, 'w', newline='') as csvfile:
    fieldnames = ['mpa_id', 'wdpa_id', 'wdpa_pid', 'name', 'designation', 'designation_eng', 'no_take_wdpa', 'no_take_mpatlas', 'no_take_area_wdpa', 'no_take_area_mpatlas']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)

    writer.writeheader()
    for row in ntchanges.values(*fieldnames):
        writer.writerow(row)

In [ ]:
for n in ntchanges:
    try:
        w_new = WdpaPoly_new.objects.get(wdpa_pid=n.wdpa_pid)
    except:
        w_new = WdpaPoint_new.objects.get(wdpa_pid=n.wdpa_pid)
    try:
        w_prev = WdpaPoly_prev.objects.filter(wdpa_pid=n.wdpa_pid)[0]
    except:
        try:
            w_prev = WdpaPoint_prev.objects.filter(wdpa_pid=n.wdpa_pid)[0]
        except:
            try:
                w_prev = WdpaPoly_prev.objects.filter(wdpaid=n.wdpa_id)[0]
            except:
                w_prev = WdpaPoint_prev.objects.filter(wdpaid=n.wdpa_id)[0]
    if (n.no_take == w_prev.no_take) or (n.no_take_area == w_prev.no_tk_area):
        print(w_new.name, w_new.desig, n.no_take_mpatlas, w_new.no_take, w_prev.no_take, n.no_take_area_mpatlas, w_new.no_tk_area, w_prev.no_tk_area)

In [ ]:
ntchanges2 = ntupdate | ntareaupdate
ntchanges.count()

In [95]:
mpaset = mpas_all_nogeom.exclude(
        Q(country__icontains='USA') | Q(sovereign__icontains='USA') |
        Q(country__icontains='UMI') | Q(sovereign__icontains='UMI') |
        Q(country__icontains='VIR') | Q(sovereign__icontains='VIR') |
        Q(country__icontains='PRI') | Q(sovereign__icontains='PRI') |
        Q(country__icontains='ASM') | Q(sovereign__icontains='ASM') |
        Q(country__icontains='GUM') | Q(sovereign__icontains='GUM') |
        Q(country__icontains='MNP') | Q(sovereign__icontains='MNP') |
        Q(country__icontains='CHL') | Q(sovereign__icontains='CHL')
#     ).exclude(
#         Q(country__icontains='MEX') | Q(country__icontains='CHL') | Q(country__icontains='IDN') | 
#         Q(country__icontains='CHN') | Q(country__icontains='JPN') | 
#         Q(sovereign__icontains='MEX') | Q(sovereign__icontains='CHL') | Q(sovereign__icontains='IDN') |
#         Q(sovereign__icontains='CHN') | Q(sovereign__icontains='JPN')
#     ).exclude(
#         Q(country__icontains='FRA') | Q(sovereign__icontains='FRA') |
#         Q(country__icontains='ATF') | Q(country__icontains='BLM') | Q(country__icontains='GLP') |
#         Q(country__icontains='GUF') | Q(country__icontains='MAF') | Q(country__icontains='MTQ') |
#         Q(country__icontains='MYT') | Q(country__icontains='NCL') | Q(country__icontains='PYF') |
#         Q(country__icontains='REU') | Q(country__icontains='SHN') | Q(country__icontains='SYC')
#     ).exclude(
#         Q(country__icontains='AUS') | Q(sovereign__icontains='AUS') |
#         Q(country__icontains='ZAF') | Q(sovereign__icontains='ZAF') |
#         Q(country__icontains='CAN') | Q(sovereign__icontains='CAN')
#     ).exclude(
#         Q(country__icontains='GBR') | Q(sovereign__icontains='GBR') |
#         Q(country__icontains='AIA') | Q(country__icontains='BMU') | Q(country__icontains='CYM') |
#         Q(country__icontains='FLK') | Q(country__icontains='GIB') | Q(country__icontains='IMN') |
#         Q(country__icontains='IOT') | Q(country__icontains='JEY') | Q(country__icontains='MSR') |
#         Q(country__icontains='PCN') | Q(country__icontains='SGS') | Q(country__icontains='SHN') |
#         Q(country__icontains='TCA') | Q(country__icontains='VGB')
    ).filter(Q())

from mpatlas.utils import cartompa
cartompa.purgeCartoMpas()

[188,
 195,
 498,
 500,
 504,
 512,
 513,
 514,
 515,
 995,
 1429,
 1431,
 1434,
 1435,
 1436,
 1437,
 1438,
 1440,
 1445,
 1503,
 1505,
 1508,
 1509,
 1510,
 1511,
 1513,
 1851,
 1872,
 2362,
 2363,
 2364,
 2365,
 2366,
 2367,
 2369,
 2370,
 2371,
 2375,
 2378,
 2510,
 2517,
 2518,
 2519,
 2522,
 2524,
 3582,
 3819,
 3820,
 3823,
 3824,
 6871,
 6884,
 6935,
 6936,
 6938,
 6942,
 6943,
 6945,
 6946,
 6948,
 6949,
 6952,
 6955,
 6956,
 6957,
 7270,
 7283,
 7299,
 9280,
 9397,
 9398,
 9399,
 9400,
 9401,
 9402,
 9403,
 9405,
 9406,
 9407,
 9408,
 9409,
 9410,
 9411,
 9412,
 9413,
 9414,
 9415,
 9416,
 9417,
 9418,
 9419,
 9420,
 9421,
 9422,
 15058,
 15083,
 7700994,
 7700999,
 7701851,
 7702510,
 7702516,
 7702520,
 7702521,
 7703821,
 7703822,
 7703825,
 7703826,
 7705349,
 7709259]

In [94]:
cartompa.updateAllMpas(mpas=mpaset)

Processing 10 of 1987 mpa records at a time
Records [0 - 9]
Records [10 - 19]
Records [20 - 29]
Records [30 - 39]
ERROR processing mpa 68807503:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807503
Records [40 - 49]
ERROR processing mpa 68807520:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807520
ERROR processing mpa 68807504:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807504
Records [50 - 59]
Records [60 - 69]
ERROR processing mpa 68807500:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807500
ERROR processing mpa 68807495:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 68807495
ERROR processing mpa 60009586:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009586
ERROR processing mpa 60009547:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009547
ERROR processing mpa 60009546:  'NoneType' object has no attribute 'hexewkb'
Skipping Mpa 60009546
ERROR processing mpa 60009495:  'NoneTyp

KeyboardInterrupt: 